In [693]:
import pandas as pd
import seaborn as sns
from ydata_profiling import ProfileReport
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error
import numpy as np
from sklearn.svm import SVR
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor,GradientBoostingRegressor
from xgboost import XGBRegressor

# Data Collection and Processing

In [694]:
teams = pd.read_csv("C:/Users/hakanirek/Desktop/data/olympic_games/teams.csv")

In [695]:
teams.head()

team      country  year  events  athletes   age  height  weight  medals  \
0  AFG  Afghanistan  1964       8         8  22.0   161.0    64.2       0   
1  AFG  Afghanistan  1968       5         5  23.2   170.2    70.0       0   
2  AFG  Afghanistan  1972       8         8  29.0   168.3    63.8       0   
3  AFG  Afghanistan  1980      11        11  23.6   168.4    63.2       0   
4  AFG  Afghanistan  2004       5         5  18.6   170.8    64.8       0   

   prev_medals  prev_3_medals  
0          0.0            0.0  
1          0.0            0.0  
2          0.0            0.0  
3          0.0            0.0  
4          0.0            0.0

In [696]:
teams= teams[["team","country","year","athletes","age","prev_medals","events","height","weight","prev_3_medals","medals",]];

In [697]:
teams.tail()

team   country  year  athletes   age  prev_medals  events  height  \
2139  ZIM  Zimbabwe  2000        26  25.0          0.0      19   179.0   
2140  ZIM  Zimbabwe  2004        14  25.1          0.0      11   177.8   
2141  ZIM  Zimbabwe  2008        16  26.1          3.0      15   171.9   
2142  ZIM  Zimbabwe  2012         9  27.3          4.0       8   174.4   
2143  ZIM  Zimbabwe  2016        31  27.5          0.0      13   167.8   

      weight  prev_3_medals  medals  
2139    71.1            0.0       0  
2140    70.5            0.0       3  
2141    63.7            1.0       4  
2142    65.2            2.3       0  
2143    62.2            2.3       0

## EDA

In [698]:
ProfileReport(teams)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [699]:
teams.corr()["medals"]

C:\Users\hakanirek\AppData\Local\Temp\ipykernel_26488\3553819720.py:1: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  teams.corr()["medals"]


year            -0.021603
athletes         0.840817
age              0.025096
prev_medals      0.920048
events           0.771330
height           0.141055
weight           0.090577
prev_3_medals    0.918438
medals           1.000000
Name: medals, dtype: float64

* Plot data and regression model fits across a FacetGrid.

In [700]:
sns.lmplot(x="athletes", y="medals", data=teams, fit_reg=True, ci=None)

In [701]:
sns.lmplot(x="prev_medals", y="medals",data=teams, fit_reg=True, ci=None)

In [702]:
teams.plot.hist(y="medals")

<AxesSubplot: ylabel='Frequency'>

### Data Cleaning

In [703]:
teams.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2144 entries, 0 to 2143
Data columns (total 11 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   team           2144 non-null   object 
 1   country        2144 non-null   object 
 2   year           2144 non-null   int64  
 3   athletes       2144 non-null   int64  
 4   age            2144 non-null   float64
 5   prev_medals    2014 non-null   float64
 6   events         2144 non-null   int64  
 7   height         2144 non-null   float64
 8   weight         2144 non-null   float64
 9   prev_3_medals  2014 non-null   float64
 10  medals         2144 non-null   int64  
dtypes: float64(5), int64(4), object(2)
memory usage: 184.4+ KB


In [704]:
# Checking for number of missing  value 
teams.isnull().sum()

team               0
country            0
year               0
athletes           0
age                0
prev_medals      130
events             0
height             0
weight             0
prev_3_medals    130
medals             0
dtype: int64

In [705]:
teams[teams.isnull().any(axis=1)]

team                           country  year  athletes   age  \
19    ALB                           Albania  1992         9  25.3   
26    ALG                           Algeria  1964         7  26.0   
39    AND                           Andorra  1976         3  28.3   
50    ANG                            Angola  1980        17  17.4   
59    ANT               Antigua and Barbuda  1976        17  23.2   
...   ...                               ...   ...       ...   ...   
2092  VIN  Saint Vincent and the Grenadines  1988         6  20.5   
2103  YAR                       North Yemen  1984         3  27.7   
2105  YEM                             Yemen  1992         8  19.6   
2112  YMD                       South Yemen  1988         5  23.6   
2120  ZAM                            Zambia  1964        15  21.7   

      prev_medals  events  height  weight  prev_3_medals  medals  
19            NaN       8   163.0    75.2            NaN       0  
26            NaN       7   175.0    65.0            NaN       0  
39            NaN       2   174.7    78.0            NaN       0  
50            NaN      14   171.7    62.5            NaN       0  
59            NaN      11   178.6    71.6            NaN       0  
...           ...     ...     ...     ...            ...     ...  
2092          NaN       6   157.0    57.0            NaN       0  
2103          NaN       3   163.3    57.7            NaN       0  
2105          NaN       8   169.0    60.0            NaN       0  
2112          NaN       5   175.0    63.3            NaN       0  
2120          NaN      13   175.7    68.0            NaN       0  

[130 rows x 11 columns]

In [706]:
teams = teams.dropna() # Remove missing values.

In [707]:
teams.head()

team      country  year  athletes   age  prev_medals  events  height  \
0  AFG  Afghanistan  1964         8  22.0          0.0       8   161.0   
1  AFG  Afghanistan  1968         5  23.2          0.0       5   170.2   
2  AFG  Afghanistan  1972         8  29.0          0.0       8   168.3   
3  AFG  Afghanistan  1980        11  23.6          0.0      11   168.4   
4  AFG  Afghanistan  2004         5  18.6          0.0       5   170.8   

   weight  prev_3_medals  medals  
0    64.2            0.0       0  
1    70.0            0.0       0  
2    63.8            0.0       0  
3    63.2            0.0       0  
4    64.8            0.0       0

## Splitting the Features and Target

In [708]:
# Training data
# Bu veri seti zamana bağlı olduğu için 2012 den önceki verileri train'e koyuyoruz
train = teams[teams["year"] < 2012].copy() # 
X_train = train.drop(columns = ["medals","year","country","team"], axis=1)
y_train= train["medals"]

# Test data
test = teams[teams["year"] >= 2012].copy()
X_test = test.drop(columns = ["medals","year","country","team"], axis=1)
y_test= test["medals"]

In [709]:
X_train

athletes   age  prev_medals  events  height  weight  prev_3_medals
0            8  22.0          0.0       8   161.0    64.2            0.0
1            5  23.2          0.0       5   170.2    70.0            0.0
2            8  29.0          0.0       8   168.3    63.8            0.0
3           11  23.6          0.0      11   168.4    63.2            0.0
4            5  18.6          0.0       5   170.8    64.8            0.0
...        ...   ...          ...     ...     ...     ...            ...
2137        28  21.2          0.0      22   171.1    62.4            5.0
2138        21  23.8          0.0      15   176.7    68.7            0.0
2139        26  25.0          0.0      19   179.0    71.1            0.0
2140        14  25.1          0.0      11   177.8    70.5            0.0
2141        16  26.1          3.0      15   171.9    63.7            1.0

[1609 rows x 7 columns]

In [710]:
y_train.head()

0    0
1    0
2    0
3    0
4    0
Name: medals, dtype: int64

In [711]:
X_train.shape

(1609, 7)

In [712]:
X_test.shape

(405, 7)

# Model Training

## Linear Regression

In [713]:
m1="Linear Regression"
reg= LinearRegression()

In [714]:
# training the model with training data
reg.fit(X_train,y_train)

# MAE on the trainin set
X_train_predict = reg.predict(X_train)
X_train_error_lr=mean_absolute_error(y_train,X_train_predict)
X_train_error_lr

# MAE on test data
X_test_predict= reg.predict(X_test)
X_test_error_lr= mean_absolute_error(y_test, X_test_predict)
X_test_error_lr

3.9397907103283374

## SVR

Linear Kernel

In [715]:
m2="SVR Linear Kernel"
svr = SVR(degree= 3, kernel="linear" )

# X_train
svr.fit(X_train, y_train)
X_train_prediction_svr = svr.predict(X_train)
X_train_error_svr = mean_absolute_error(y_train,X_train_prediction_svr)
print(X_train_error_svr)

# X_test
X_test_prediction_svr = svr.predict(X_test)
X_test_error_svr_linear = mean_absolute_error(y_test,X_test_prediction_svr)
print(X_test_error_svr_linear)

4.256590390762696
3.305685839216148


Polnoymial Kernel

In [716]:
m3="SVR Poly Kernel"
svr = SVR(degree= 3, kernel="poly" )

# X_train
svr.fit(X_train, y_train)
X_train_prediction_svr = svr.predict(X_train)
X_train_error_svr = mean_absolute_error(y_train,X_train_prediction_svr)
print(X_train_error_svr)

# X_test
X_test_prediction_svr = svr.predict(X_test)
X_test_error_svr_poly = mean_absolute_error(y_test,X_test_prediction_svr)
print(X_test_error_svr_poly)


3.9520823279637387
2.9821920352435916


# XGB

In [717]:
m4="XGB"
xgb = XGBRegressor(n_estimators=300, max_depth=6, learning_rate=0.01,
                   subsample= 0.25,  )

xgb.fit(X_train, y_train)
# Accuracy on training data
X_train_predict_xgb= xgb.predict(X_train)
X_train_error_xgb = mean_absolute_error(y_train, X_train_predict_xgb)
print(X_train_error_xgb)


 # Accuracy on test data
X_test_predict_xgb = xgb.predict(X_test)
X_test_error_xgb = mean_absolute_error(y_test, X_test_predict_xgb)
print(X_test_error_xgb)


3.1658096692071633
3.1447843817281136


## Extreme Gradient Boost

In [718]:
m5="Extreme Gradient Boost"
Egb = GradientBoostingRegressor(n_estimators=200, subsample= 0.20, 
                                max_depth=3,)
# training the model with training data
Egb.fit(X_train,y_train)

# Accuracy on training data
X_train_predict_Egb= Egb.predict(X_train)
X_train_error_Egb = mean_absolute_error(y_train, X_train_predict_Egb)
print(X_train_error_Egb)


 # Accuracy on test data
X_test_predict_Egb = Egb.predict(X_test)
X_test_error_Egb = mean_absolute_error(y_test, X_test_predict_Egb)
print(X_test_error_Egb)


2.7265524462497712
3.8465821580317123


# Result

In [719]:

results = {"Models": [m1, m2, m3 ,m4, m5],
           "MAE": [X_test_error_lr, X_test_error_svr_linear, X_test_error_svr_poly,X_test_error_xgb, X_test_error_Egb]}
    
for (key, value) in results.items():
    if key=="Accuracy":
        results[key]=  [item*100 for item in results[key]]

    
result_df=pd.DataFrame(results)


In [720]:
result_df

Models       MAE
0       Linear Regression  3.939791
1       SVR Linear Kernel  3.305686
2         SVR Poly Kernel  2.982192
3                     XGB  3.144784
4  Extreme Gradient Boost  3.846582

## Prediction with Best Model SVR Poly Kernel

In [721]:
# SVR Poly Kernel

X_test_prediction_svr = svr.predict(X_test)
X_test_error_svr_poly = mean_absolute_error(y_test,X_test_prediction_svr)
print(X_test_error_svr_poly)

2.9821920352435916


In [722]:
# Create a predictions column in test dataset
test["predictions"]= X_test_prediction_svr
test

team      country  year  athletes   age  prev_medals  events  height  \
6     AFG  Afghanistan  2012         6  24.8          1.0       6   171.7   
7     AFG  Afghanistan  2016         3  24.7          1.0       3   173.7   
24    ALB      Albania  2012        10  25.7          0.0       9   176.8   
25    ALB      Albania  2016         6  23.7          0.0       6   176.2   
37    ALG      Algeria  2012        39  24.8          2.0      29   174.3   
...   ...          ...   ...       ...   ...          ...     ...     ...   
2111  YEM        Yemen  2016         3  19.3          0.0       3   169.7   
2131  ZAM       Zambia  2012         7  22.6          0.0       7   176.2   
2132  ZAM       Zambia  2016         7  24.1          0.0       7   175.2   
2142  ZIM     Zimbabwe  2012         9  27.3          4.0       8   174.4   
2143  ZIM     Zimbabwe  2016        31  27.5          0.0      13   167.8   

      weight  prev_3_medals  medals  predictions  
6       60.8            0.3       1     0.037221  
7       74.0            0.7       0     0.036976  
24      80.2            0.0       0    -0.009888  
25      67.2            0.0       0    -0.069941  
37      66.9            2.3       1     0.957877  
...      ...            ...     ...          ...  
2111    65.7            0.0       0    -0.101316  
2131    74.2            0.0       0    -0.058744  
2132    67.5            0.0       0    -0.057106  
2142    65.2            2.3       0     0.502952  
2143    62.2            2.3       0     0.550349  

[405 rows x 12 columns]

In [723]:
# if predictions value is less than 0 it will be equal to 0
test.loc[test["predictions"] < 0, "predictions"] = 0
test

team      country  year  athletes   age  prev_medals  events  height  \
6     AFG  Afghanistan  2012         6  24.8          1.0       6   171.7   
7     AFG  Afghanistan  2016         3  24.7          1.0       3   173.7   
24    ALB      Albania  2012        10  25.7          0.0       9   176.8   
25    ALB      Albania  2016         6  23.7          0.0       6   176.2   
37    ALG      Algeria  2012        39  24.8          2.0      29   174.3   
...   ...          ...   ...       ...   ...          ...     ...     ...   
2111  YEM        Yemen  2016         3  19.3          0.0       3   169.7   
2131  ZAM       Zambia  2012         7  22.6          0.0       7   176.2   
2132  ZAM       Zambia  2016         7  24.1          0.0       7   175.2   
2142  ZIM     Zimbabwe  2012         9  27.3          4.0       8   174.4   
2143  ZIM     Zimbabwe  2016        31  27.5          0.0      13   167.8   

      weight  prev_3_medals  medals  predictions  
6       60.8            0.3       1     0.037221  
7       74.0            0.7       0     0.036976  
24      80.2            0.0       0     0.000000  
25      67.2            0.0       0     0.000000  
37      66.9            2.3       1     0.957877  
...      ...            ...     ...          ...  
2111    65.7            0.0       0     0.000000  
2131    74.2            0.0       0     0.000000  
2132    67.5            0.0       0     0.000000  
2142    65.2            2.3       0     0.502952  
2143    62.2            2.3       0     0.550349  

[405 rows x 12 columns]

In [724]:
test["predictions"] = test["predictions"].round()
test

team      country  year  athletes   age  prev_medals  events  height  \
6     AFG  Afghanistan  2012         6  24.8          1.0       6   171.7   
7     AFG  Afghanistan  2016         3  24.7          1.0       3   173.7   
24    ALB      Albania  2012        10  25.7          0.0       9   176.8   
25    ALB      Albania  2016         6  23.7          0.0       6   176.2   
37    ALG      Algeria  2012        39  24.8          2.0      29   174.3   
...   ...          ...   ...       ...   ...          ...     ...     ...   
2111  YEM        Yemen  2016         3  19.3          0.0       3   169.7   
2131  ZAM       Zambia  2012         7  22.6          0.0       7   176.2   
2132  ZAM       Zambia  2016         7  24.1          0.0       7   175.2   
2142  ZIM     Zimbabwe  2012         9  27.3          4.0       8   174.4   
2143  ZIM     Zimbabwe  2016        31  27.5          0.0      13   167.8   

      weight  prev_3_medals  medals  predictions  
6       60.8            0.3       1          0.0  
7       74.0            0.7       0          0.0  
24      80.2            0.0       0          0.0  
25      67.2            0.0       0          0.0  
37      66.9            2.3       1          1.0  
...      ...            ...     ...          ...  
2111    65.7            0.0       0          0.0  
2131    74.2            0.0       0          0.0  
2132    67.5            0.0       0          0.0  
2142    65.2            2.3       0          1.0  
2143    62.2            2.3       0          1.0  

[405 rows x 12 columns]

In [726]:
# USA 
test[test["team"]=="USA"]

team        country  year  athletes   age  prev_medals  events  height  \
2053  USA  United States  2012       689  26.7        317.0     245   178.3   
2054  USA  United States  2016       719  26.4        248.0     245   178.0   

      weight  prev_3_medals  medals  predictions  
2053    74.7          274.0     248        261.0  
2054    73.8          276.0     264        258.0

In [727]:
# INDIA
test[test["team"]=="IND"]

team country  year  athletes   age  prev_medals  events  height  weight  \
907  IND   India  2012        95  26.0          3.0      55   174.2    72.7   
908  IND   India  2016       130  26.1          6.0      67   170.0    66.3   

     prev_3_medals  medals  predictions  
907            1.7       6          3.0  
908            3.3       2          5.0

In [755]:
medals_by_country =test["predictions"].groupby(test["country"]).mean()

In [753]:
medals_by_country.shape

(205,)

In [754]:
df = pd.DataFrame(medals_by_country)
df.tail(50)

predictions
country                                      
Saint Kitts and Nevis                     0.0
Saint Lucia                               0.0
Saint Vincent and the Grenadines          0.0
Samoa                                     0.0
San Marino                                0.0
Sao Tome and Principe                     0.0
Saudi Arabia                              0.0
Senegal                                   0.0
Serbia                                   19.0
Seychelles                                0.0
Sierra Leone                              0.0
Singapore                                 2.0
Slovakia                                  7.0
Slovenia                                  6.0
Solomon Islands                           0.0
South Africa                             16.0
South Korea                              93.0
Spain                                   111.0
Sri Lanka                                 0.0
Sudan                                     0.0
Suriname                                  0.0
Swaziland                                 0.0
Sweden                                   27.0
Switzerland                               7.0
Switzerland-1                             7.0
Syria                                     0.0
Tajikistan                                0.0
Tanzania                                  0.0
Thailand                                  3.0
Timor Leste                               0.0
Togo                                      0.0
Tonga                                     0.0
Trinidad and Tobago                       4.0
Tunisia                                   5.0
Turkey                                   10.0
Turkmenistan                              0.0
Tuvalu                                    0.0
Uganda                                    0.0
Ukraine                                  53.0
United Arab Emirates                      0.0
United States                           519.0
United States Virgin Islands              0.0
Uruguay                                   0.0
Uzbekistan                                5.0
Vanuatu                                   0.0
Venezuela                                 5.0
Vietnam                                   0.0
Yemen                                     0.0
Zambia                                    0.0
Zimbabwe                                  2.0